# 后向折叠 dense 的测试用例

In [1]:
%cd ..
import set_env

/media/pc/data/lxw/ai/tvm-book/tests/book/doc/tests


In [2]:
import numpy as np

import tvm
from tvm import relay
from tvm.relay import transform
# from tvm.relay.testing import create_workload
# from tvm.relay.build_module import bind_params_by_name


def initializer(_, param):
    param = np.zeros(param.shape)


def _get_positive_scale(size):
    return np.random.uniform(0.5, 1, size=size).astype("float32")


def run_opt_pass(expr, opt_pass):
    assert isinstance(opt_pass, tvm.transform.Pass)
    mod = tvm.IRModule.from_expr(expr)
    mod = opt_pass(mod)
    entry = mod["main"]
    return entry if isinstance(expr, relay.Function) else entry.body

In [3]:
def before(x, weight, in_bias, in_scale):
    args = [x, weight, in_bias]
    x = relay.nn.dense(x, weight)
    x = relay.add(x, in_bias)
    x = relay.nn.relu(x)
    y = relay.multiply(x, in_scale)
    return relay.Function(args, y)

def expected(x, weight, in_bias, in_scale):
    # use a fixed order of args so alpha equal check can pass
    args = [x, weight, in_bias]
    scale = relay.expand_dims(in_scale, axis=1)
    weight = relay.multiply(weight, scale)
    x = relay.nn.dense(x, weight)
    bias = relay.multiply(in_bias, in_scale)
    x = relay.add(x, bias)
    y = relay.nn.relu(x)
    return relay.Function(args, y)

In [4]:
def check(data_shape, weight_shape):
    x = relay.var("x", shape=data_shape)
    weight = relay.var("weight", shape=weight_shape)
    out_channels = weight_shape[0]
    in_bias = relay.var("in_bias", shape=(out_channels,))
    in_scale = relay.const(_get_positive_scale((out_channels,)))
    y1 = before(x, weight, in_bias, in_scale)
    y1 = run_opt_pass(y1, transform.InferType())
    print("FoldScaleAxis 前：")
    tvm.IRModule.from_expr(y1).show()

    y1_folded = run_opt_pass(y1, transform.BackwardFoldScaleAxis())
    y1_expected = expected(x, weight, in_bias, in_scale)

    y1_folded = run_opt_pass(y1_folded, transform.InferType())
    print("FoldScaleAxis 后：")
    tvm.IRModule.from_expr(y1_folded).show()
    
    y1_expected = run_opt_pass(y1_expected, transform.InferType())
    tvm.ir.assert_structural_equal(y1_folded, y1_expected)

check((2, 4), (3, 4))
check((3, 5), (4, 5))

FoldScaleAxis 前：


FoldScaleAxis 后：


FoldScaleAxis 前：


FoldScaleAxis 后：
